In [1]:
import org.apache.spark.sql.SparkSession
val sc = SparkSession.builder().getOrCreate()
sc.version

sc = org.apache.spark.sql.SparkSession@7cd14c79


2.4.3

### 7. 집계 연산

집계를 수행하려면 **키, 그룹**을 지정하고 하나 이상의 컬럼을 변환하는 방법을 지정하는 **집계 함수**를 사용함 <br> 
집계 함수는 여러 입력 값이 주어지면 그룹별로 결과를 생성함.<br> 
<br> 
다음과 같은 그룹화 데이터 타입을 생성할 수 있다. <br> 
- 가장 간단한 형태의 그룹화는 select 구문에서 집계를 수행해 Dataframe의 전체 데이터를 요약함
- group by는 하나 이상의 키를 지정하며, 값을 가진 칼럼을 변환하기 위해 다른 집계 함수를 사용할 수 있음
- window 는 하나 이상의 키를 지정하며, 값을 가진 칼럼을 변환하기 위해 사른 집계 함수를 사용할 수 있음. 하지만 함수의 입력으로 사용할 로우는 현재 로우와 어느정도 연관성이 있어야 함(?)
- grouping set 은 서로 다른 레벨의 값을 집계할 때 사용함. SQL, DataFrame의 롤업, 큐브를 사용할 수 있음
- rollup은 하나 이상의 키를 지정하며, 컬럼을 변환하는데 다른 집계 함수를 사용하여 계층적으로 요약된 값을 구함
- cube는 하나 이상의 키를 지정하며, 컬럼을 변환하는데 다른 집계 함수를 사용할 수 있고, 모든 컬럼 조합에 대한 요약된 값을 구함

In [5]:
// 데이터 읽음
// 적은 수로 분할할 수 있도록 리파티셔닝 진행하며 빠르게 접근할 수 있도록 캐싱.
val df = sc.read.format("csv").option("header", "true").option("inferSchema","true").load("./all/*.csv").coalesce(5)
df.unpersist()
df.cache()
df.createOrReplaceTempView("dfTable")
df.show(5, false)

+---------+---------+-----------------------------------+--------+--------------+---------+----------+--------------+
|InvoiceNo|StockCode|Description                        |Quantity|InvoiceDate   |UnitPrice|CustomerID|Country       |
+---------+---------+-----------------------------------+--------+--------------+---------+----------+--------------+
|536365   |85123A   |WHITE HANGING HEART T-LIGHT HOLDER |6       |12/1/2010 8:26|2.55     |17850     |United Kingdom|
|536365   |71053    |WHITE METAL LANTERN                |6       |12/1/2010 8:26|3.39     |17850     |United Kingdom|
|536365   |84406B   |CREAM CUPID HEARTS COAT HANGER     |8       |12/1/2010 8:26|2.75     |17850     |United Kingdom|
|536365   |84029G   |KNITTED UNION FLAG HOT WATER BOTTLE|6       |12/1/2010 8:26|3.39     |17850     |United Kingdom|
|536365   |84029E   |RED WOOLLY HOTTIE WHITE HEART.     |6       |12/1/2010 8:26|3.39     |17850     |United Kingdom|
+---------+---------+-----------------------------------

df = [InvoiceNo: string, StockCode: string ... 6 more fields]


[InvoiceNo: string, StockCode: string ... 6 more fields]

In [6]:
// 간단한 집계
// count()는 action 이기 때문에 바로 결과를 반환함.
df.count() == 541909

true

### 7.1 집계 함수
집계 함수는 org.apache.spark.sql.functions 패키지에서 찾아볼 수 있음

In [7]:
// count
import org.apache.spark.sql.functions.count
df.select(count("StockCode")).show()

+----------------+
|count(StockCode)|
+----------------+
|          541909|
+----------------+



In [8]:
// countDistinct
import org.apache.spark.sql.functions.countDistinct
df.select(countDistinct("StockCode")).show()

+-------------------------+
|count(DISTINCT StockCode)|
+-------------------------+
|                     4070|
+-------------------------+



In [11]:
// approx_count_distinct: 근사치 count로 최대 추정 오류율이라는 파라미터를 사용함.
// 근사치를 계산하지만, countDistinct 함수보다 빠르게 결과를 반환함
// 대규모 데이터 셋을 사용할 수록 더 빠른 성능을 보임.
import org.apache.spark.sql.functions.approx_count_distinct
df.select(approx_count_distinct("StockCode", 0.1)).show()

+--------------------------------+
|approx_count_distinct(StockCode)|
+--------------------------------+
|                            3364|
+--------------------------------+



In [12]:
// first, last
import org.apache.spark.sql.functions.{first, last}
df.select(first("StockCode"), last("StockCode")).show()

+-----------------------+----------------------+
|first(StockCode, false)|last(StockCode, false)|
+-----------------------+----------------------+
|                 85123A|                 22138|
+-----------------------+----------------------+



In [14]:
// min, max
import org.apache.spark.sql.functions.{min, max}
df.select(min("Quantity"), max("Quantity")).show()

+-------------+-------------+
|min(Quantity)|max(Quantity)|
+-------------+-------------+
|       -80995|        80995|
+-------------+-------------+



In [15]:
//sum
import org.apache.spark.sql.functions.{sum}
df.select(sum("Quantity")).show()

+-------------+
|sum(Quantity)|
+-------------+
|      5176450|
+-------------+



In [16]:
// sumDinsinct: 고유값을 합산함
import org.apache.spark.sql.functions.{sumDistinct}
df.select(sumDistinct("Quantity")).show()

+----------------------+
|sum(DISTINCT Quantity)|
+----------------------+
|                 29310|
+----------------------+



In [19]:
// avg
import org.apache.spark.sql.functions.{avg, sum, count, expr}
df.select(
    count("Quantity").alias("total_transactions"),
    sum("Quantity").alias("total_purchases"),
    avg("Quantity").alias("avg_purchases"),
    expr("mean(Quantity)").alias("mean_purchases")
).show()

+------------------+---------------+----------------+----------------+
|total_transactions|total_purchases|   avg_purchases|  mean_purchases|
+------------------+---------------+----------------+----------------+
|            541909|        5176450|9.55224954743324|9.55224954743324|
+------------------+---------------+----------------+----------------+



In [21]:
// 분산, 표준편차
// 분산과 표준편차는 데이터가 분포된 정도를 측정하는 방법.
// 표본표준편차(samp), 모표준편차(pop) 방식을 지원함.
import org.apache.spark.sql.functions.{var_pop, stddev_pop}
import org.apache.spark.sql.functions.{var_samp, stddev_samp}

df.select(var_pop("Quantity"), var_samp("Quantity"),
         stddev_pop("Quantity"), stddev_samp("Quantity")).show()

+------------------+------------------+--------------------+---------------------+
| var_pop(Quantity)|var_samp(Quantity)|stddev_pop(Quantity)|stddev_samp(Quantity)|
+------------------+------------------+--------------------+---------------------+
|47559.303646609354| 47559.39140929905|  218.08095663447864|   218.08115785023486|
+------------------+------------------+--------------------+---------------------+



In [22]:
// 비대칭도와 첨도
// 데이터의 변곡점을 측정하는 방법 (확률변수, 확률분포로 데이터를 모델링할 때 중요함)
// 비대칭도: 데이터 평균의 비대칭 정도를 측정
// 첨도: 데이터 끝 부분을 측정함.
import org.apache.spark.sql.functions.{skewness, kurtosis}

df.select(skewness("Quantity"), kurtosis("Quantity")).show()

+--------------------+------------------+
|  skewness(Quantity)|kurtosis(Quantity)|
+--------------------+------------------+
|-0.26407557610527843|119768.05495536518|
+--------------------+------------------+



In [25]:
//공분산, 상관관계
// cov, corr를 통해 공분산, 상관관계를 계산할 수 있음.
// 공분산: 데이터 입력 값에 따라 다른 범위를 가짐 (얜 표본공분산, 모공분산을 계산할 수 있음)
// 상관관계: 피어슨 상관계수를 측정하여 -1,1 사이의 값을 가짐.
import org.apache.spark.sql.functions.{corr, covar_pop, covar_samp}

df.select(corr("InvoiceNo", "Quantity"), covar_pop("InvoiceNo", "Quantity"),
         covar_samp("InvoiceNo", "Quantity")).show()

+-------------------------+------------------------------+-------------------------------+
|corr(InvoiceNo, Quantity)|covar_pop(InvoiceNo, Quantity)|covar_samp(InvoiceNo, Quantity)|
+-------------------------+------------------------------+-------------------------------+
|     4.912186085637639E-4|            1052.7260778752732|             1052.7280543913773|
+-------------------------+------------------------------+-------------------------------+



In [26]:
// 복합 데이터 타입의 집계
// 복합 데이터 타입을 사용해 집계를 수행할 수 있음. 예를 들어 특정 칼럼의 값을 리스트로 수집하거나 셋 데이터 타입으로 고윳값만 수집할 수 있음.
import org.apache.spark.sql.functions.{collect_set, collect_list}
df.agg(collect_set("Country"),collect_list("Country")).show(5, false)

+--------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

----------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

----------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

----------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

----------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

...

----------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

----------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

----------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

----------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



### 7.2 그룹화

Dataframe 수준의 집계 뿐만 아니라, 데이터 그룹 기반의 집계를 수행하는 경우가 더 많음. <br>
데이터 그룹 기반의 집계는 단일 컬럼의 데이터를 그룹화하고 해당 그룹의 다른 여러 컬럼을 사용해 계산하기 위해 카테고리형 데이터를 사용함. <br>
그룹의 기준이 되는 컬럼을 여러 개 지정할 수 있음.

In [33]:
// 그룹화
// 집계를 하나만 쓸땐, 바로 집계함수를 사용 (count())
df.groupBy("InvoiceNo", "CustomerId").count().show(5, false)

+---------+----------+-----+
|InvoiceNo|CustomerId|count|
+---------+----------+-----+
|536846   |14573     |76   |
|537026   |12395     |12   |
|537883   |14437     |5    |
|538068   |17978     |12   |
|538279   |14952     |7    |
+---------+----------+-----+
only showing top 5 rows



In [31]:
// 표현식을 이용한 그룹화
// 집계를 여러 사용하고 싶을 떄, agg(집계 함수1, 집계 함수2, 집계 함수3)
import org.apache.spark.sql.functions.count

df.groupBy("InvoiceNo").agg(
    count("Quantity").alias("quan"),
    avg("Quantity").alias("avg"),
    expr("count(Quantity)")
).show(5, false)

+---------+----+------------------+---------------+
|InvoiceNo|quan|avg               |count(Quantity)|
+---------+----+------------------+---------------+
|536596   |6   |1.5               |6              |
|536938   |14  |33.142857142857146|14             |
|537252   |1   |31.0              |1              |
|537691   |20  |8.15              |20             |
|538041   |1   |30.0              |1              |
+---------+----+------------------+---------------+
only showing top 5 rows



In [34]:
// 맵을 이용한 그룹화
df.groupBy("InvoiceNo").agg("Quantity"->"avg", "Quantity"->"stddev_pop").show()

+---------+------------------+--------------------+
|InvoiceNo|     avg(Quantity)|stddev_pop(Quantity)|
+---------+------------------+--------------------+
|   536596|               1.5|  1.1180339887498947|
|   536938|33.142857142857146|  20.698023172885524|
|   537252|              31.0|                 0.0|
|   537691|              8.15|   5.597097462078001|
|   538041|              30.0|                 0.0|
|   538184|12.076923076923077|   8.142590198943392|
|   538517|3.0377358490566038|  2.3946659604837897|
|   538879|21.157894736842106|  11.811070444356483|
|   539275|              26.0|  12.806248474865697|
|   539630|20.333333333333332|  10.225241100118645|
|   540499|              3.75|  2.6653642652865788|
|   540540|2.1363636363636362|  1.0572457590557278|
|  C540850|              -1.0|                 0.0|
|   540976|10.520833333333334|   6.496760677872902|
|   541432|             12.25|  10.825317547305483|
|   541518| 23.10891089108911|  20.550782784878713|
|   541783|1

### 7.3 윈도우 함수

특정 **윈도우** 를 대상으로 집계 연산을 수행함. <br>

group-by와 차이점?
- group-by를 사용하면 **Dataframe**에 모든 로우 레코드에 대한 결괎값을 계산함.
- 허나, 윈도우 함수는 **프레임**에 입력되는 모든 로우에 대한 결괎값을 계산함. (프레임: 로우 그룹 기반의 테이블을 뜻하며, 각 로우는 하나 이상의 프레임에 할당될 수 있음)

세가지 종류의 운도우 함수를 지원함
- 랭크 함수
- 분석 함수
- 집계 함수

In [36]:
// 윈도우함수를 위해 date 컬럼이 필요하다. (InvoceDate에서 날짜 정보만 추출)
import org.apache.spark.sql.functions.{col, to_date}

val dfWithDate = df.withColumn("date", to_date(col("InvoiceDate"), "MM/d/yyyy H:mm"))
dfWithDate.createOrReplaceTempView("dfWithDate")
dfWithDate.show(5, false)

+---------+---------+-----------------------------------+--------+--------------+---------+----------+--------------+----------+
|InvoiceNo|StockCode|Description                        |Quantity|InvoiceDate   |UnitPrice|CustomerID|Country       |date      |
+---------+---------+-----------------------------------+--------+--------------+---------+----------+--------------+----------+
|536365   |85123A   |WHITE HANGING HEART T-LIGHT HOLDER |6       |12/1/2010 8:26|2.55     |17850     |United Kingdom|2010-12-01|
|536365   |71053    |WHITE METAL LANTERN                |6       |12/1/2010 8:26|3.39     |17850     |United Kingdom|2010-12-01|
|536365   |84406B   |CREAM CUPID HEARTS COAT HANGER     |8       |12/1/2010 8:26|2.75     |17850     |United Kingdom|2010-12-01|
|536365   |84029G   |KNITTED UNION FLAG HOT WATER BOTTLE|6       |12/1/2010 8:26|3.39     |17850     |United Kingdom|2010-12-01|
|536365   |84029E   |RED WOOLLY HOTTIE WHITE HEART.     |6       |12/1/2010 8:26|3.39     |17850 

dfWithDate = [InvoiceNo: string, StockCode: string ... 7 more fields]


[InvoiceNo: string, StockCode: string ... 7 more fields]

In [46]:
import org.apache.spark.sql.expressions.Window
import org.apache.spark.sql.functions.col

// 윈도우 명세 생성
// partitionBy()는 파티셔닝 스키마의 개념이 아닌, 그룹을 어떻게 나눌지 결정함 (프레임 만드는 과정)
// orderBy()는 파티션 정렬 방식을 정의
// rowsBetween() 입력된 로우의 참조를 기반으로 프레임에 로우가 포함될 수 있는지 결정함. 아래 예제는 첫 로우, 현재 로우까지 확인. (?)
val windowSpec = Window.partitionBy("CustomerId", "date").orderBy(col("Quantity").desc)
                    .rowsBetween(Window.unboundedPreceding, Window.currentRow)

import org.apache.spark.sql.functions.{max, dense_rank, rank}

val maxPurchaseQuantity = max(col("Quantity")).over(windowSpec) //시간대별 최대 구매 개수를 구하는 예제
val purchaseDenseRank = dense_rank().over(windowSpec) // 모든 고객에 대해 최대 구매수량을 가진 날짜가
val purchaseRank = rank().over(windowSpec)

dfWithDate.where("CustomerId IS NOT NULL").orderBy("CustomerId")
    .select(
        col("CustomerId") ,
        col("date"),
        col("Quantity"),
        purchaseRank.alias("quantityRank") ,
        purchaseDenseRank.alias("quantityDenseRank") ,
        maxPurchaseQuantity.alias("maxPurchaseQuantity")
    ).show(50, false)

+----------+----------+--------+------------+-----------------+-------------------+
|CustomerId|date      |Quantity|quantityRank|quantityDenseRank|maxPurchaseQuantity|
+----------+----------+--------+------------+-----------------+-------------------+
|12346     |2011-01-18|74215   |1           |1                |74215              |
|12346     |2011-01-18|-74215  |2           |2                |74215              |
|12347     |2010-12-07|36      |1           |1                |36                 |
|12347     |2010-12-07|30      |2           |2                |36                 |
|12347     |2010-12-07|24      |3           |3                |36                 |
|12347     |2010-12-07|12      |4           |4                |36                 |
|12347     |2010-12-07|12      |4           |4                |36                 |
|12347     |2010-12-07|12      |4           |4                |36                 |
|12347     |2010-12-07|12      |4           |4                |36           

windowSpec = org.apache.spark.sql.expressions.WindowSpec@73f71d3c
maxPurchaseQuantity = max(Quantity) OVER (PARTITION BY CustomerId, date ORDER BY Quantity DESC NULLS LAST ROWS BETWEEN UNBOUNDED PRECEDING AND CURRENT ROW)
purchaseDenseRank = DENSE_RANK() OVER (PARTITION BY CustomerId, date ORDER BY Quantity DESC NULLS LAST ROWS BETWEEN UNBOUNDED PRECEDING AND CURRENT ROW)
purchaseRank = RANK() OVER (PARTITION BY CustomerId, date ORDER BY Quantity DESC NULLS LAST ROWS BETWEEN UNBOUNDED PRECEDING AND CURRENT ROW)


lastException: Throwable = null


RANK() OVER (PARTITION BY CustomerId, date ORDER BY Quantity DESC NULLS LAST ROWS BETWEEN UNBOUNDED PRECEDING AND CURRENT ROW)